In [1]:
import pandas as pd
from modeling.utils import load_config
from bertopic import BERTopic
import numpy as np
from tqdm import tqdm
tqdm.pandas()
import torch
config = load_config()


2024-06-10 21:43:48.483684: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-06-10 21:43:48.535968: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-06-10 21:43:49.450448: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
embeddings = np.load("../data/processed/Document_Embeddings.npy")

In [3]:
embeddings

array([[ 0.07162705, -0.5124514 , -0.35952565, ..., -0.27501535,
        -0.3400203 ,  0.31884128],
       [ 0.07464305, -0.41961193, -0.17686662, ..., -0.3495943 ,
        -0.24562414,  0.35183027],
       [ 0.11793648, -0.518762  , -0.23346135, ..., -0.19809987,
        -0.4267902 ,  0.19690108],
       ...,
       [ 0.25113267, -0.37451935, -0.11767858, ..., -0.15912151,
        -0.2908483 ,  0.49034804],
       [ 0.05632647, -0.07859585, -0.23251684, ...,  0.01553675,
        -0.0969719 ,  0.36347044],
       [ 0.09254633, -0.32474533, -0.27699035, ..., -0.04035068,
        -0.24767956,  0.67027795]], dtype=float32)

# QDrant

In [4]:
from modeling.search_model import NeuralSearcher
# Create a neural searcher instance
neural_searcher = NeuralSearcher(collection_name="PMC-Patient", raw_corpus=config['proc_paths']['DATA_PATH'],
                                 corpus_cls=config['corpus']['pmc_cls_corpus'], embeddings=embeddings)

result =  neural_searcher.sub_query_search(query="Heart")

res_df = neural_searcher.show_results(result)

No sentence-transformers model found with name Charangan/MedBERT. Creating a new one with mean pooling.


In [5]:
res_df

[{'id': 100783,
  'score': 0.8957964,
  'patient_uid': '7490198-2',
  'PMID': 32924340,
  'title': 'Usefulness of Nested Polymerase Chain Reaction with Clinical Specimens for Diagnosis of Leptospirosis: a Case Series and a Review of Literature',
  'patient': 'A 73-year-old Korean female was admitted to the emergency room with a 6-day history of headache, myalgia, fever, and chills on August 9, 2007. She had no medical history. She reported that she had worked in the fields 10 days before the admission. She presented with fever (37.7°C). Laboratory results showed white blood cells of 13,480/µL, hemoglobin of 10.4 g/dL, and platelets of 96 × 103/µL. A lumbar puncture test was normal. The antibody titer using PHA was negative at admission. Supportive treatment was performed considering that the fever was due to a viral infection. However, the antibody titer 10 days after symptom onset was 1:5,120. At the same time, Leptospira spp. N-PCR with urine was positive, and also, N-PCR with plasma

In [6]:
result

{74272: 0.87562823,
 38116: 0.8723927499999999,
 99475: 0.8784359675,
 36816: 0.87118477,
 160551: 0.8710184,
 51354: 0.87016606,
 23738: 0.8693111,
 131245: 0.86897093,
 111471: 0.8688944,
 106989: 0.8777771125,
 112202: 0.867615,
 157364: 0.8673732,
 16122: 0.8671638,
 95264: 0.8671112,
 83012: 0.86696655,
 71297: 0.86635613,
 130020: 0.867674795,
 20558: 0.8662478,
 81501: 0.86615026,
 96403: 0.86614615,
 131575: 0.88820696,
 39786: 0.88679755,
 42819: 0.8848299,
 166974: 0.87313805,
 59726: 0.882426,
 148696: 0.88195163,
 75357: 0.87450775,
 44877: 0.8798873,
 156199: 0.8791712,
 161997: 0.87834346,
 27574: 0.8771131,
 37617: 0.87708914,
 575: 0.8769857,
 161684: 0.87690663,
 95659: 0.87595576,
 23480: 0.87592244,
 95040: 0.8753104,
 43778: 0.8753036,
 161697: 0.8750584,
 88742: 0.87492895,
 42838: 0.88373744,
 144442: 0.87971365,
 40035: 0.875799,
 114536: 0.8745168,
 130362: 0.87297124,
 48578: 0.8725267,
 848: 0.8713974,
 48871: 0.8711773,
 91844: 0.8698482,
 48577: 0.86982876,


In [7]:
def getPPRnPAR(results):
    PPR = []
    PAR = []
    
    for i in results:
        PPR.append(i['patient_uid'])
        PAR.append(i['PMID'])

    return { "PPR": PPR, "PAR": PAR}


def _deconstruct(Qresults, q, df_par, df_ppr):
    par, ppr = Qresults[q]['PAR'], Qresults[q]['PPR']
    PAR_relevant = df_par[df_par['query-id'] == q]['corpus-id'].values.tolist()
    PPR_relevant = df_ppr[df_ppr['query-id'] == q]['corpus-id'].values.tolist()
    return par, ppr, PAR_relevant, PPR_relevant

def p_10(Qresults, q, df_par, df_ppr):
    par, ppr, PAR_relevant, PPR_relevant  = _deconstruct(Qresults, q, df_par, df_ppr)
    par_p10 = np.mean([1 if pr in PAR_relevant else 0 for pr in par[:10]])

    ppr_p10 = np.mean([1 if pr in PPR_relevant else 0 for pr in ppr[:10]])
    
    return par_p10, ppr_p10, f"{par_p10=} and {ppr_p10=}"
    
    
def mean_average_precision(Qresults, query_ids, df_par, df_ppr):

    MAP_par = []
    MAP_ppr = []
    n = len(query_ids)
    
    for q in tqdm(query_ids, total=n):
        par, ppr, PAR_relevant, PPR_relevant  = _deconstruct(Qresults, q, df_par, df_ppr)
        n_par = len(PAR_relevant)
        n_ppr = len(PPR_relevant)

        avg_ppr = []
        avg_par = []
        
        for i, val in enumerate(par):
            for id in par:
                if len(avg_par) == n_par:
                    break
                if id in PAR_relevant:
                    avg_par.append(1)
                else:
                    avg_par.append(0)
            
        for i, val in enumerate(ppr):
            for id in ppr:
                if len(avg_ppr) == n_ppr:
                    break
                if id in PPR_relevant:
                    avg_ppr.append(1)
                else:
                    avg_ppr.append(0)
        
        MAP_par.append(np.mean(avg_par))
        MAP_ppr.append(np.mean(avg_ppr))
    
    MAP_ppr = np.mean(MAP_ppr)
    MAP_par = np.mean(MAP_par)
    
    return MAP_par, MAP_ppr, f"{MAP_ppr=}, {MAP_ppr=}"
    
    
def r_precision(Qresults, q, df_par, df_ppr):
    par, ppr, PAR_relevant, PPR_relevant  = _deconstruct(Qresults, q, df_par, df_ppr)
    par_len, ppr_len = len(PAR_relevant), len(PPR_relevant)
    par_rel = par[:par_len]
    ppr_rel = ppr[:ppr_len]

    par_rp = np.mean([1 if pr in PAR_relevant else 0 for pr in par_rel])

    ppr_rp = np.mean([1 if pr in PPR_relevant else 0 for pr in ppr_rel])
    
    return par_rp, ppr_rp, f"{par_rp=} and {ppr_rp=}"



In [8]:
Queries = config['test']['query']
ppr_q = config['test']['ppr']
par_q = config['test']['par']

In [9]:
test_ppr = pd.read_csv(ppr_q, sep='\t')
test_par = pd.read_csv(par_q, sep='\t')

In [10]:
queries_text = pd.read_json(Queries, orient='records', lines=True)

In [11]:
ls_ppr = set(test_ppr['query-id'].tolist())
ls_par = set(test_par['query-id'].tolist())

In [12]:
common_queries = list(ls_par & ls_ppr)

In [13]:
test_pprC = test_ppr[test_ppr['query-id'].isin(common_queries)].reset_index(drop=True)
test_parC = test_par[test_par['query-id'].isin(common_queries)].reset_index(drop=True)
queries_text = queries_text[queries_text['_id'].isin(common_queries)].reset_index(drop=True)

In [14]:
test_parC

query-id  corpus-id  score
0      8647806-1   30625055      1
1      8647806-1   22931316      1
2      8647806-1   29922935      1
3      8647806-1   30918173      1
4      8647806-1   25160558      1
...          ...        ...    ...
62311  3996740-1   32864093      1
62312  3996740-1   15020367      1
62313  3996740-1   25312972      1
62314  3996740-1   23986837      1
62315  3996740-1   24761084      1

[62316 rows x 3 columns]

In [15]:
queries_text

_id                                               text
0     8647806-1  A 70-year-old Caucasian woman with medical his...
1     8654082-1  A female patient aged 27 years presented with ...
2     8677995-1  An eighty year-old female presented with bleed...
3     6006860-1  A 20-year-old female patient presented to our ...
4     6007063-1  An 11-year, 7-month-old girl visited the Kyung...
...         ...                                                ...
2807  3985785-1  In April 2013, a 71-year-old female with no si...
2808  3990081-1  A 51-year-old woman with a history of bipolar ...
2809  3994690-1  A 29-year-old African-American male was admitt...
2810  3995396-1  A 75-year-old right-handed female patient was ...
2811  3996740-1  A 28-year-old female presented with complaint ...

[2812 rows x 2 columns]

In [16]:
inference_results = {}
from tqdm import tqdm

for i, row in tqdm(queries_text.iterrows(), desc="Iterating Queries", total=len(common_queries)):
    q_id = row['_id']
    text = row['text']
    q_res = neural_searcher.sub_query_search(text)
    extract_info = neural_searcher.show_results(q_res)
    inference_results[q_id] = getPPRnPAR(extract_info)


Iterating Queries: 100%|██████████| 2812/2812 [2:13:35<00:00,  2.85s/it]  


In [18]:
len(inference_results.keys())

2812

In [19]:
import pickle

# with open('../InferenceResults/Test2812.pkl', 'wb') as f:
#     pickle.dump(inference_results, f)

with open('../InferenceResults/Test2812.pkl', 'rb') as f:
    inference_r = pickle.load(f)


In [20]:
inference_r

{'8647806-1': {'PPR': ['8307750-1',
   '4931935-2',
   '2983013-1',
   '3948856-1',
   '8570721-2',
   '6057278-1',
   '4318041-1',
   '8383673-2',
   '8383673-3',
   '5821964-1',
   '5649836-1',
   '6718791-1',
   '6837768-1',
   '3713602-2',
   '6330528-2',
   '7454860-4',
   '3519074-1',
   '8316963-1',
   '6180816-1',
   '4479923-1'],
  'PAR': [34359303,
   27382562,
   21120166,
   24624217,
   34754218,
   30073101,
   25657435,
   34434416,
   34434416,
   29515924,
   29147278,
   31531332,
   31754479,
   23936717,
   30666080,
   32964179,
   23248696,
   34368322,
   30363554,
   26170577]},
 '8654082-1': {'PPR': ['3738333-1',
   '3318266-1',
   '6311218-1',
   '6159296-1',
   '4052052-1',
   '2955228-1',
   '4166642-1',
   '6695537-1',
   '4212400-1',
   '7360192-1',
   '4142949-1',
   '5695022-1',
   '8554436-1',
   '3168563-1',
   '4532116-1',
   '8316963-1',
   '6718791-1',
   '4736760-1',
   '7475761-1',
   '6380075-1',
   '4107219-1',
   '3420220-1',
   '3335648-1',
  

In [21]:
query_ids = list(inference_r.keys())

In [22]:
query_ids[0]

'8647806-1'

In [23]:
inference_results = inference_r.copy()
for qd in query_ids:
    inf = inference_results[qd]
    par_p10, ppr_p10, summary = p_10(inference_results, qd, 
         df_par=test_parC, df_ppr=test_pprC)
    inf['par_p10'] = par_p10
    inf['ppr_p10'] = ppr_p10
    print(str(qd) + " "+ summary)

8647806-1 par_p10=0.0 and ppr_p10=0.0
8654082-1 par_p10=0.0 and ppr_p10=0.0
8677995-1 par_p10=0.0 and ppr_p10=0.0
6006860-1 par_p10=0.0 and ppr_p10=0.0
6007063-1 par_p10=0.0 and ppr_p10=0.0
6011191-1 par_p10=0.0 and ppr_p10=0.0
6016128-1 par_p10=0.0 and ppr_p10=0.0
6016161-1 par_p10=0.0 and ppr_p10=0.0
6022268-1 par_p10=0.0 and ppr_p10=0.0
6027982-1 par_p10=0.0 and ppr_p10=0.0
6029733-1 par_p10=0.0 and ppr_p10=0.0
6032649-1 par_p10=0.0 and ppr_p10=0.0
6039681-1 par_p10=0.0 and ppr_p10=0.0
6040207-1 par_p10=0.0 and ppr_p10=0.0
6063379-1 par_p10=0.1 and ppr_p10=0.0
6064627-1 par_p10=0.0 and ppr_p10=0.0
6066556-1 par_p10=0.0 and ppr_p10=0.0
6066715-1 par_p10=0.0 and ppr_p10=0.0
6078126-1 par_p10=0.0 and ppr_p10=0.0
6079612-1 par_p10=0.0 and ppr_p10=0.0
6081099-1 par_p10=0.0 and ppr_p10=0.0
6089491-1 par_p10=0.0 and ppr_p10=0.0
6097304-1 par_p10=0.1 and ppr_p10=0.0
6099025-1 par_p10=0.0 and ppr_p10=0.0
6099025-2 par_p10=0.0 and ppr_p10=0.0
6100695-1 par_p10=0.1 and ppr_p10=0.0
6101515-1 pa

In [24]:
for qd in query_ids:
    inf = inference_results[qd]
    par_rp, ppr_rp, summary = r_precision(inference_results, qd, 
         df_par=test_parC, df_ppr=test_pprC)
    inf['par_rp'] = par_rp
    inf['ppr_rp'] = ppr_rp
    print(str(qd) + " "+ summary)

8647806-1 par_rp=0.0 and ppr_rp=0.0
8654082-1 par_rp=0.0 and ppr_rp=0.0
8677995-1 par_rp=0.0 and ppr_rp=0.0
6006860-1 par_rp=0.0 and ppr_rp=0.0
6007063-1 par_rp=0.0 and ppr_rp=0.0
6011191-1 par_rp=0.0 and ppr_rp=0.0
6016128-1 par_rp=0.0 and ppr_rp=0.0
6016161-1 par_rp=0.0 and ppr_rp=0.0
6022268-1 par_rp=0.0 and ppr_rp=0.0
6027982-1 par_rp=0.0 and ppr_rp=0.0
6029733-1 par_rp=0.0 and ppr_rp=0.0
6032649-1 par_rp=0.0 and ppr_rp=0.0
6039681-1 par_rp=0.0 and ppr_rp=0.0
6040207-1 par_rp=0.0 and ppr_rp=0.0
6063379-1 par_rp=0.08333333333333333 and ppr_rp=0.0
6064627-1 par_rp=0.0 and ppr_rp=0.0
6066556-1 par_rp=0.0 and ppr_rp=0.0
6066715-1 par_rp=0.0 and ppr_rp=0.0
6078126-1 par_rp=0.0 and ppr_rp=0.0
6079612-1 par_rp=0.0 and ppr_rp=0.0
6081099-1 par_rp=0.0 and ppr_rp=0.0
6089491-1 par_rp=0.0 and ppr_rp=0.0
6097304-1 par_rp=0.08333333333333333 and ppr_rp=0.0
6099025-1 par_rp=0.0 and ppr_rp=0.0
6099025-2 par_rp=0.0 and ppr_rp=0.0
6100695-1 par_rp=0.14285714285714285 and ppr_rp=0.0
6101515-1 par_rp

In [25]:
MAP_par, MAP_ppr, sum_map = mean_average_precision(inference_results, query_ids, df_par=test_parC, df_ppr=test_pprC)

100%|██████████| 2812/2812 [00:09<00:00, 290.97it/s]


In [27]:
inference_results['MAP_PAR'] = MAP_par
inference_results['MAP_PPR'] = MAP_ppr

In [1]:
sum_map

NameError: name 'sum_map' is not defined

In [29]:
# with open('../InferenceResults/CompleteTest.pkl', 'wb') as f:
#     pickle.dump(inference_results, f)

with open('../InferenceResults/CompleteTest.pkl', 'rb') as f:
    inference_complete = pickle.load(f)

In [30]:
inference_complete

{'8647806-1': {'PPR': ['8307750-1',
   '4931935-2',
   '2983013-1',
   '3948856-1',
   '8570721-2',
   '6057278-1',
   '4318041-1',
   '8383673-2',
   '8383673-3',
   '5821964-1',
   '5649836-1',
   '6718791-1',
   '6837768-1',
   '3713602-2',
   '6330528-2',
   '7454860-4',
   '3519074-1',
   '8316963-1',
   '6180816-1',
   '4479923-1'],
  'PAR': [34359303,
   27382562,
   21120166,
   24624217,
   34754218,
   30073101,
   25657435,
   34434416,
   34434416,
   29515924,
   29147278,
   31531332,
   31754479,
   23936717,
   30666080,
   32964179,
   23248696,
   34368322,
   30363554,
   26170577],
  'par_p10': 0.0,
  'ppr_p10': 0.0,
  'par_rp': 0.0,
  'ppr_rp': 0.0},
 '8654082-1': {'PPR': ['3738333-1',
   '3318266-1',
   '6311218-1',
   '6159296-1',
   '4052052-1',
   '2955228-1',
   '4166642-1',
   '6695537-1',
   '4212400-1',
   '7360192-1',
   '4142949-1',
   '5695022-1',
   '8554436-1',
   '3168563-1',
   '4532116-1',
   '8316963-1',
   '6718791-1',
   '4736760-1',
   '7475761-

In [34]:
# with open('../InferenceResults/CompleteTest_Metrics.pkl', 'wb') as f:
#     pickle.dump(inferences, f)

with open('../InferenceResults/CompleteTest_Metrics.pkl', 'rb') as f:
    inference_met = pickle.load(f)



In [35]:
from pprint import pprint
pprint(inference_met)

{'1618844-1': {'PAR': [30800272,
                       22919398,
                       22919398,
                       23986824,
                       25061588,
                       22567530,
                       25250159,
                       20981201,
                       1807369,
                       30647951,
                       31423442,
                       32664076,
                       24753647,
                       34046474,
                       26236526,
                       26933463,
                       29147392,
                       34104407,
                       31440480,
                       23691385,
                       30363338,
                       25539876,
                       22956963,
                       34457238,
                       26101687,
                       23483761,
                       21991519],
               'PPR': ['6380075-1',
                       '3420220-1',
                       '3420220-2',
 